# Visualize / Stack `gctree` visualizations

This notebook will read in the gctree svg's from each PR and stack them into single images for easier comparison.

In [10]:
import os
import sys

import pandas as pd
import svg_stack as ss
from IPython.display import SVG as ip_SVG
from IPython.display import display as ip_display
import svgutils.transform as sg
from svgutils.compose import *

In [11]:
manifest_path = '../metadata.PR2.csv'
results_dir = "results/gctrees"
svg_filename = "delta_bind.svg"
# svg_filename = "gctree.inference.1.svg"
output_dir = "output/gctree_svg_stack_imm_duration"

In [12]:
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

manifest_df = pd.read_csv(manifest_path)
manifest_df.head()
# manifest_df.query(f"PR == 2.01")

PR imm_duration strain  mouse  plate   gc node cell_type  hc_barcode  \
0  2.01          d15     wt     10      1  10B   LP        GC          16   
1  2.01          d15     wt      1      2   1A   RP        GC           9   
2  2.01          d15     wt      1      3   1C   RI        GC           2   
3  2.01          d15     wt      1      4   1D   LI        GC          14   
4  2.01          d15     wt      2      5   2A   RP        GC          10   

   lc_barcode              row                         col  
0          10  A.B.C.D.E.F.G.H  1.2.3.4.5.6.7.8.9.10.11.12  
1           9  A.B.C.D.E.F.G.H  1.2.3.4.5.6.7.8.9.10.11.12  
2           1  A.B.C.D.E.F.G.H  1.2.3.4.5.6.7.8.9.10.11.12  
3           2  A.B.C.D.E.F.G.H  1.2.3.4.5.6.7.8.9.10.11.12  
4          11  A.B.C.D.E.F.G.H  1.2.3.4.5.6.7.8.9.10.11.12

In [13]:
print(manifest_df.PR.unique())

[2.01 2.02 2.03 2.04]


In [14]:

# def create_subpanel(svg_path, annotation, position, scale=0.5):

# loop through each row, and find the corresponding tree in the results directory named "PR<PR>-<mouse>-<node>-<gc>-GC"
for duration, duration_df in manifest_df.groupby('imm_duration'):
    # Create an empty figure
    fig = sg.SVGFigure()

    # Initial y position for stacking
    y_offset = 60
    all_panels = []
    all_panels.append(Text(f"IMM Duration: {duration}", 550, 15, size=16, weight='bold'))

    for pr, pr_df in duration_df.groupby('PR'):

        pr_str = f"{pr:.2f}"

        for i, row in pr_df.iterrows():

            position=(10, y_offset)
            svg_path = f"{results_dir}/PR{pr_str}-{row['mouse']}-{row['node']}-{row['gc']}-GC/{svg_filename}"
            annotation = f"PR: {pr_str}, Mouse: {row['mouse']}, Node: {row['node']}, GC: {row['gc']}"
            # print(svg_path)
            if not os.path.exists(svg_path):
                print(f"Skipping {svg_path}")
                # panel = Panel(
                #   Text(f"(!) No tree found for: {annotation}", 10, 0, size=12, weight='bold', color="red")
                # #   Text(f"(!) No tree found for: {svg_path}", 10, 0, size=12, weight='bold', color="red")
                # ).move(*position)
                # all_panels.append(panel)
            else:
                # Create a subpanel
                panel = Panel(
                        SVG(svg_path).scale(0.3),
                        Text(annotation, 10, -15, size=12, weight='bold')
                ).move(*position)
                all_panels.append(panel)

            y_offset += 250

    fig = Figure("%dpx" % 1250, "%dpx" % y_offset, *all_panels)
    fig.save(f"{output_dir}/{duration}.{svg_filename}")
    ip_display(ip_SVG(f"{output_dir}/{duration}.{svg_filename}"))

Skipping results/gctrees/PR2.02-12-LP-12B-GC/delta_bind.svg
Skipping results/gctrees/PR2.04-1-RP-1B-GC/delta_bind.svg
